In [0]:
# loading data with inferred schema

from pyspark.sql.functions import input_file_name, explode, split

filename = "/FileStore/tables/loan*"
df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/FileStore/tables/loan_top250k.csv")

df.createOrReplaceTempView("loanData")


In [0]:
len(df.collect())

Out[ 2 ]: 250000

In [0]:
# Displaying the top 10 rows of the dataframe for inspection

sqlDF = spark.sql("select count(*) from loanData ")
display(sqlDF)

count(1) 250000

In [0]:
# the default schema is all strings so we'll need to remedy this

df.printSchema()

root
-- id: string (nullable = true)
-- member_id: string (nullable = true)
-- loan_amnt: integer (nullable = true)
-- funded_amnt: integer (nullable = true)
-- funded_amnt_inv: double (nullable = true)
-- term: string (nullable = true)
-- int_rate: double (nullable = true)
-- installment: double (nullable = true)
-- grade: string (nullable = true)
-- sub_grade: string (nullable = true)
-- emp_title: string (nullable = true)
-- emp_length: string (nullable = true)
-- home_ownership: string (nullable = true)
-- annual_inc: double (nullable = true)
-- verification_status: string (nullable = true)
-- issue_d: string (nullable = true)
-- loan_status: string (nullable = true)
-- pymnt_plan: string (nullable = true)
-- url: string (nullable = true)
-- desc: string (nullable = true)
-- purpose: string (nullable = true)
-- title: string (nullable = true)
-- zip_code: string (nullable = true)
-- addr_state: string (nullable = true)
-- dti: double (nullable = true)
-- delinq_2yrs: integer (nullable = true)
-- earliest_cr_line: string (nullable = true)
-- inq_last_6mths: integer (nullable = true)
-- mths_since_last_delinq: double (nullable = true)
-- mths_since_last_record: double (nullable = true)
-- open_acc: integer (nullable = true)
-- pub_rec: integer (nullable = true)
-- revol_bal: integer (nullable = true)
-- revol_util: double (nullable = true)
-- total_acc: integer (nullable = true)
-- initial_list_status: string (nullable = true)
-- out_prncp: double (nullable = true)
-- out_prncp_inv: double (nullable = true)
-- total_pymnt: double (nullable = true)
-- total_pymnt_inv: double (nullable = true)
-- total_rec_prncp: double (nullable = true)
-- total_rec_int: double (nullable = true)
-- total_rec_late_fee: double (nullable = true)
-- recoveries: double (nullable = true)
-- collection_recovery_fee: double (nullable = true)
-- last_pymnt_d: string (nullable = true)
-- last_pymnt_amnt: double (nullable = true)
-- next_pymnt_d: string (nullable = true)
-- last_credit_pull_d: string (nullable = true)
-- collections_12_mths_ex_med: integer (nullable = true)
-- mths_since_last_major_derog: double (nullable = true)
-- policy_code: integer (nullable = true)
-- application_type: string (nullable = true)
-- annual_inc_joint: double (nullable = true)
-- dti_joint: double (nullable = true)
-- verification_status_joint: string (nullable = true)
-- acc_now_delinq: integer (nullable = true)
-- tot_coll_amt: integer (nullable = true)
-- tot_cur_bal: integer (nullable = true)
-- open_acc_6m: integer (nullable = true)
-- open_act_il: integer (nullable = true)
-- open_il_12m: integer (nullable = true)
-- open_il_24m: integer (nullable = true)
-- mths_since_rcnt_il: double (nullable = true)
-- total_bal_il: integer (nullable = true)
-- il_util: double (nullable = true)
-- open_rv_12m: integer (nullable = true)
-- open_rv_24m: integer (nullable = true)
-- max_bal_bc: integer (nullable = true)
-- all_util: double (nullable = true)
-- total_rev_hi_lim: integer (nullable = true)
-- inq_fi: integer (nullable = true)
-- total_cu_tl: integer (nullable = true)
-- inq_last_12m: integer (nullable = true)
-- acc_open_past_24mths: integer (nullable = true)
-- avg_cur_bal: double (nullable = true)
-- bc_open_to_buy: double (nullable = true)
-- bc_util: double (nullable = true)
-- chargeoff_within_12_mths: integer (nullable = true)
-- delinq_amnt: integer (nullable = true)
-- mo_sin_old_il_acct: double (nullable = true)
-- mo_sin_old_rev_tl_op: integer (nullable = true)
-- mo_sin_rcnt_rev_tl_op: integer (nullable = true)
-- mo_sin_rcnt_tl: integer (nullable = true)
-- mort_acc: integer (nullable = true)
-- mths_since_recent_bc: double (nullable = true)
-- mths_since_recent_bc_dlq: double (nullable = true)
-- mths_since_recent_inq: double (nullable = true)
-- mths_since_recent_revol_delinq: double (nullable = true)
-- num_accts_ever_120_pd: integer (nullable = true)
-- num_actv_bc_tl: integer (nullable = true)
-- num_actv_rev_tl: integer (nullable = true)
-- num_bc_

In [0]:
# Inspecting our dependent variable. 

df.groupBy("loan_status").count().sort("loan_status",ascending=False).show()

+------------------+------+
 loan_status| count|
+------------------+------+
Late (31-120 days)| 1914|
 Late (16-30 days)| 460|
 In Grace Period| 1163|
 Fully Paid| 10358|
 Default| 2|
 Current|235536|
 Charged Off| 567|
+------------------+------+

In [0]:
# converting our variable to binary depending on whether or not it was a charge off
from pyspark.sql.functions import when

df = df.withColumn("isChargeOff",when(df.loan_status == 'Charged Off', 1).otherwise(0))

df.groupBy("isChargeOff").count().sort("isChargeOff",ascending=False).show()

+-----------+------+
isChargeOff| count|
+-----------+------+
 1| 567|
 0|249433|
+-----------+------+

In [0]:
# filling blank continous values as 0
df = df.na.fill(0)

In [0]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler

In [0]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler
categoricalColumns = ["verification_status", "term", "grade", "sub_grade"]
stages = [] # stages in our Pipeline
for categoricalCol in categoricalColumns:
    # Category Indexing with StringIndexer
    stringIndexer = StringIndexer(inputCol=categoricalCol, outputCol=categoricalCol + "Index")
    # Use OneHotEncoder to convert categorical variables into binary SparseVectors
    # encoder = OneHotEncoderEstimator(inputCol=categoricalCol + "Index", outputCol=categoricalCol + "classVec")
    encoder = OneHotEncoderEstimator(inputCols=[stringIndexer.getOutputCol()], outputCols=[categoricalCol + "classVec"])
    # Add stages.  These are not run here, but will run all at once later on.
    stages += [stringIndexer, encoder]

In [0]:
# Convert label into label indices using the StringIndexer
label_stringIdx = StringIndexer(inputCol="isChargeOff", outputCol="label")
stages += [label_stringIdx]

In [0]:
# Transform all features into a vector using VectorAssembler
numericCols = ["loan_amnt",	"funded_amnt",	"funded_amnt_inv", "annual_inc"]
assemblerInputs = [c + "classVec" for c in categoricalColumns] + numericCols
assembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")
stages += [assembler]

In [0]:
from sklearn.svm import LinearSVC
from sklearn.feature_selection import RFE
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [0]:
svm = LinearSVC()
recurFS = RFE(svm, 5)#used Recursive Feature Elimination for the feature selection
recurFS = recurFS.fit(df,np.ravel(,order='C'))
print(recurFS.support_)#gives the result of attributes that are used to find the fake accounts
print(recurFS.ranking_)#gives the rank for the attributes

--------------------------------------------------------------------------- 
 TypeError Traceback (most recent call last)
 <command-1194925677402493> in <module> () 
 1 svm = LinearSVC ( ) 
 2 recurFS = RFE ( svm , 5 ) #used Recursive Feature Elimination for the feature selection 
 ----> 3 recurFS = recurFS . fit ( df , np . ravel ( order = 'C' ) ) 
 4 print ( recurFS . support_ ) #gives the result of attributes that are used to find the fake accounts 
 5 print ( recurFS . ranking_ ) #gives the rank for the attributes 

 TypeError : ravel() missing 1 required positional argument: 'a'

In [0]:
from pyspark.ml.classification import LogisticRegression
  
partialPipeline = Pipeline().setStages(stages)
pipelineModel = partialPipeline.fit(df)
preppedDataDF = pipelineModel.transform(df)

In [0]:
### Randomly split data into training and test sets. set seed for reproducibility
(trainingData, testData) = preppedDataDF.randomSplit([0.7, 0.3], seed=100)
print(trainingData.count())
print(testData.count())

175341
74659

In [0]:
from pyspark.ml.classification import LogisticRegression

# Create initial LogisticRegression model
lr = LogisticRegression(labelCol="label", featuresCol="features", maxIter=50)

# Train model with Training Data
lrModel = lr.fit(trainingData)

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator

# Evaluate model
predictions = lrModel.transform(testData)
evaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")
evaluator.evaluate(predictions)

Out[ 15 ]: 0.713654565521297

In [0]:
display(predictions)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term isChargeOff verification_statusIndex verification_statusclassVec termIndex termclassVec gradeIndex gradeclassVec sub_gradeIndex sub_gradeclassVec label features rawPrediction probability prediction null null 1000 1000 750.0 36 months 10.33 32.43 B B1 Resource teacher 2 years MORTGAGE 54000.0 Source Verified Dec-2018 Current n null null debt_consolidation Debt consolidation 871xx NM 4.37 2 Feb-1998 0 11.0 0.0 5 0 6283 16.8 15 f 952.15 714.11 64.29 48.22 47.85 16.44 0.0 0.0 0.0 Feb-2019 32.43 Mar-2019 Feb-2019 1 12.0 1 Individual 0.0 0.0 null 0 0 154754 0 0 0 0 74.0 0 0.0 0 0 4854 17.0 37500 0 0 0 1 30951.0 31217.0 16.8 0 0 74.0 250 41 18 2 41.0 0.0 0.0 0.0 1 3 3 4 9 1 4 11 3 5 0.0 0 1 0 86.7 0.0 0 0 197500 6283 37500 0 0.0 null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 N null null null 0.0 0.0 null null null 0.0 0.0 null 0.0 0.0 0.0 Cash N null null null 0.0 0.0 0.0 0 1.0 List(0, 2, List(1), List(1.0)) 0.0 List(0, 1, List(0), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 8.0 List(0, 34, List(8), List(1.0)) 0.0 List(0, 47, List(1, 2, 4, 17, 43, 44, 45, 46), List(1.0, 1.0, 1.0, 1.0, 1000.0, 1000.0, 750.0, 54000.0)) List(1, 2, List(), List(6.339828685192818, -6.339828685192818)) List(1, 2, List(), List(0.9982385038302689, 0.001761496169731182)) 0.0 null null 1000 1000 750.0 36 months 12.98 33.69 B B5 teacher 10+ years RENT 95000.0 Not Verified Dec-2018 Current n null null vacation Vacation 606xx IL 9.1 1 May-2004 1 17.0 0.0 10 0 2968 10.1 18 f 954.01 715.5 65.58 49.19 45.99 19.59 0.0 0.0 0.0 Feb-2019 33.69 Mar-2019 Feb-2019 0 0.0 1 Individual 0.0 0.0 null 0 930 19910 2 2 1 2 4.0 16942 56.0 2 2 1987 33.0 29500 2 0 1 4 1991.0 19058.0 10.1 0 0 175.0 97 5 4 0 35.0 0.0 4.0 17.0 0 3 6

In [0]:
y_true = predictions.select(["isChargeOff"]).collect()
y_true

Out[ 17 ]: [Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),
 Row(isChargeOff=0),

In [0]:
y_pred = predictions.select(['prediction']).collect.map(_.toSeq)
from sklearn.metrics import classification_report, confusion_matrix
print(classification_report(y_true, y_pred))

--------------------------------------------------------------------------- 
 AttributeError Traceback (most recent call last)
 <command-948599561129557> in <module> () 
 ----> 1 y_pred = predictions . select ( [ 'prediction' ] ) . collect . map ( _ . toSeq ) 
 2 from sklearn . metrics import classification_report , confusion_matrix 
 3 print ( classification_report ( y_true , y_pred ) ) 

 AttributeError : 'function' object has no attribute 'map'

In [0]:
display(trainingData)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term isChargeOff verification_statusIndex verification_statusclassVec termIndex termclassVec gradeIndex gradeclassVec sub_gradeIndex sub_gradeclassVec label features null null 1000 1000 725.0 36 months 10.72 32.61 B B2 Server 2 years RENT 48000.0 Not Verified Dec-2018 Current n null null other Other 060xx CT 6.2 0 Dec-2012 0 0.0 0.0 10 0 9866 24.0 12 f 952.44 690.52 64.62 46.85 47.56 17.06 0.0 0.0 0.0 Feb-2019 32.61 Mar-2019 Feb-2019 0 0.0 1 Individual 0.0 0.0 null 0 0 19363 1 2 1 1 9.0 9497 99.0 3 5 6890 38.0 41100 1 0 2 6 1936.0 27846.0 24.1 0 0 62.0 72 3 3 0 3.0 0.0 9.0 0.0 0 5 6 6 7 3 8 9 6 10 0.0 0 0 4 100.0 0.0 0 0 50650 19363 36700 9550 0.0 null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 N null null null 0.0 0.0 null null null 0.0 0.0 null 0.0 0.0 0.0 Cash N null null null 0.0 0.0 0.0 0 0.0 List(0, 2, List(0), List(1.0)) 0.0 List(0, 1, List(0), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 4.0 List(0, 34, List(4), List(1.0)) 0.0 List(0, 47, List(0, 2, 4, 13, 43, 44, 45, 46), List(1.0, 1.0, 1.0, 1.0, 1000.0, 1000.0, 725.0, 48000.0)) null null 1000 1000 725.0 36 months 11.31 32.89 B B3 null null RENT 24000.0 Not Verified Dec-2018 Current n null null other Other 148xx NY 2.05 0 Feb-1999 0 0.0 0.0 1 0 4147 23.7 4 f 952.85 690.82 65.15 47.23 47.15 18.0 0.0 0.0 0.0 Feb-2019 32.89 Mar-2019 Feb-2019 0 0.0 1 Individual 0.0 0.0 null 0 0 4147 0 0 0 1 21.0 0 0.0 0 0 4147 24.0 17500 0 0 0 1 4147.0 13353.0 23.7 0 0 21.0 238 25 21 0 25.0 0.0 0.0 0.0 0 1 1 1 2 1 1 3 1 1 0.0 0 0 0 100.0 0.0 0 0 17500 4147 17500 0 0.0 null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 N null null null 0.0 0.0 null null null 0.0 0.0 null 0.0 0.0 0.0 Cash N null null null 0.0 0.0 0.0 0 0.0 List(0, 2, List(0), List(1.0))

In [0]:
from pyspark.ml.classification import DecisionTreeClassifier

# Create initial Decision Tree Model
dt = DecisionTreeClassifier(labelCol="label", featuresCol="features", maxDepth=30)

# Train model with Training Data
dtModel = dt.fit(trainingData)

In [0]:
print("numNodes = ", dtModel.numNodes)
print("depth = ", dtModel.depth)

numNodes = 1133
depth = 28

In [0]:
predictions = dtModel.transform(testData)

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator
# Evaluate model
evaluator = BinaryClassificationEvaluator()
evaluator.evaluate(predictions)

Out[ 23 ]: 0.3428883283711466